In [1]:
from DeepLearning.Environments.CatanEnv import CatanEnv, SelfPlayDistribution
from DeepLearning.PPO import MaskablePPO
from DeepLearning.GetActionMask import getActionMask
from DeepLearning.GetObservation import getObservation, getObservationSimplified, lowerBoundsSimplified, upperBoundsSimplified
from Agents.AgentModel import AgentMultiModel
from Agents.AgentRandom2 import AgentRandom2
from Agents.AgentNoMoves import AgentNoMoves
import os


os.environ["UPDATE_MODELS"] = "False"
os.environ["MODEL_NAME"] = "None"
os.environ["VP_REWARDS"] = "False"
os.environ["WIN_REWARDS"] = "False"
os.environ["MODEL_1_NAME"] = ""
os.environ["MODEL_2_NAME"] = ""
os.environ["MODEL_3_NAME"] = ""

env = SelfPlayDistribution()

info = {
    "env": "CatanEnv",
    "Timesteps": "1M",
    "Opponents": "self.play",
    "Rewards": "Setup, Dense, Bank Trades"
}
name = "SelfPlayDistribution"

netArchDict = dict(pi=[128, 128], vf=[128, 128])

# model = MaskablePPO("MlpPolicy", env, policy_kwargs=dict(net_arch=netArchDict), gamma=0.4, verbose=1, getActionMask=getActionMask, getObservation=getObservationSimplified, info=info, saveName=name, tensorboard_log="./tensorboard_logs/")
model=MaskablePPO.load("DeepLearning/Models/BaselineSelfPlay/BaselineSelfPlay.zip", env=env)
model.saveName = name
model.learn(total_timesteps=50_000, tb_log_name=f"{name}")


Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard_logs/SelfPlaySame_5


/Users/danieldrummond/Catan/PyCatron/TC2/Client/env/lib/python3.11/site-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_masks to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.action_masks` for environment variables or `env.get_wrapper_attr('action_masks')` that will search the reminding wrappers.
  logger.warn(


---------------------------------
| rollout/           |          |
|    ep_len_mean     | 59.9     |
|    ep_rew_mean     | 94.1     |
| time/              |          |
|    fps             | 582      |
|    iterations      | 1        |
|    time_elapsed    | 3        |
|    total_timesteps | 2048     |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 55          |
|    ep_rew_mean          | 92.4        |
| time/                   |             |
|    fps                  | 478         |
|    iterations           | 2           |
|    time_elapsed         | 8           |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.031121306 |
|    clip_fraction        | 0.295       |
|    clip_range           | 0.2         |
|    entropy_loss         | -1.09       |
|    explained_variance   | -0.324      |
|    learning_rate        | 0.

/Users/danieldrummond/Catan/PyCatron/TC2/Client/env/lib/python3.11/site-packages/stable_baselines3/common/save_util.py:283: UserWarning: Path 'DeepLearning/Models/SelfPlaySame' does not exist. Will create it.
  warnings.warn(f"Path '{path.parent}' does not exist. Will create it.")


-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 63.1        |
|    ep_rew_mean          | 108         |
| time/                   |             |
|    fps                  | 430         |
|    iterations           | 17          |
|    time_elapsed         | 80          |
|    total_timesteps      | 34816       |
| train/                  |             |
|    approx_kl            | 0.037071202 |
|    clip_fraction        | 0.309       |
|    clip_range           | 0.2         |
|    entropy_loss         | -1.01       |
|    explained_variance   | -0.0262     |
|    learning_rate        | 0.0003      |
|    loss                 | 3.94        |
|    n_updates            | 920         |
|    policy_gradient_loss | -0.0312     |
|    value_loss           | 10.2        |
-----------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 63.9  

RuntimeError: [enforce fail at inline_container.cc:424] . unexpected pos 2176 vs 2070

In [13]:
# Test Trained model using env format, use to debug running environments 

from sb3_contrib.common.maskable.utils import get_action_masks
from DeepLearning.Environments.NoSetupEnv import NoSetupDenseRewardEnv, NoSetupEnv
from DeepLearning.Environments.SetupEnv import SetupRandomWithRoadsEnv
from DeepLearning.Environments.CatanEnv import CatanEnv, GAME_RESULTS
from DeepLearning.Environments.SelfPlayEnv import SelfPlayEnv, SelfPlaySetupDotTotalEnv
import os
from Game.CatanPlayer import PlayerStatsTracker
from DeepLearning.PPO import MaskablePPO
from Agents.AgentRandom2 import AgentRandom2
from Agents.AgentNoMoves import AgentNoMoves
from Agents.AgentMCTS import AgentMCTS
from tabulate import tabulate
from DeepLearning.Stats import headers
import pandas as pd
import random
from CatanData.GameStateViewer import SaveGameStateImage, DisplayImage
import time
from collections import deque

os.environ["UPDATE_MODELS"] = "False"
os.environ["MODEL_NAME"] = "None"

model=MaskablePPO.load("DeepLearning/Models/Full/Rewards_SetupVpActionDenseTrades_18M.zip")

rewardList = []
winner = [0,0,0,0]

players = [ AgentRandom2("P0", 0),
            AgentNoMoves("P1", 1),
            AgentNoMoves("P2", 2),
            AgentNoMoves("P3", 3),]

env = CatanEnv(players=players)

total_actions = 0

for episode in range(500):
    done = False
    state, info = env.reset()#players=players)

    while done != True:
        action_masks = get_action_masks(env)
        action, _states = model.predict(state, action_masks=action_masks)
        state, reward, done, _, info = env.step(action.item())
        rewardList.append(reward)
        total_actions += 1

    winner[env.game.gameState.winner] += 1
    
    # env.game.gameState.players[0].generatePlayerStats()
    # env.game.gameState.players[3].generatePlayerStats()

    # print(env.game.gameState.players[0].stats)
    # DisplayImage(env.game.gameState)
    # print(rewardList[-1] - 25)
print(rewardList)
print(sum(rewardList))

print(f"TotalActions:{total_actions}")
print("\n\nWinnings: ", winner)

print(GAME_RESULTS)


# Brick, ore, wool, wheat, wood

[0, 0, 17.25, 0, 1, -0.9375, 0, 0, 0, 0.5, 0, 0, 0.5, 0, 1, 0.75, 1, -0.1875, 1.5, 14, 18, 0.5, 0, -2, -0.1875, 1.5, 4, 1, 0.5, 0, 3.0, 10, 0.5, 0, 0, 0, -0.1875, 1.5, 4, 1, 0, 0, 1.5, 4, -0.1875, 1, 0.5, 0, 10, 1.5, 4, 10, 1, 0, 0, 4, 21, 0.5, 0, 1.5, 0, 0, 18.0, 0, -0.1875, -0.1875, 0, 14, 4, 1.5, 4, 1, 0, 1, 0, 1.5, 4, -0.1875, 21, 0, -1.6875, -0.1875, 0, 0.75, 1, 0, 0.75, 1.5, -1.6875, 10, 0, 0, -1.6875, -1.6875, -0.1875, 0, 0, 0, 0, 3.0, 10, -0.1875, 0, 0.75, 20, 1.5, 0, -0.1875, 0, 0, 0, 10, 3.75, 10, 0, 0, 15.75, 0, 1, 1, -2, 18, 0, -2, -2, 0, -2, -2, 0, -0.1875, -2, -0.1875, 10, 0, 10, 0, 0, -0.1875, 0, 0, 0, 0, 0, 4.5, 10, 4, 1, 0, 0, 0, 14, 3.0, 0, 0, 0, 0, 5.25, 4, 1, 0, 0, 0, 0.75, 0.75, 5.25, 14, -0.1875, -0.1875, 1.5, 4, 21, 0, 3.75, 0, 0, 18.75, 0, 14, 14, 0, 0, 14, 0, 0.5, 0, 14, 4, 1, 0, 10, -0.1875, 0, -0.1875, 4, 4, -0.1875, 1, 0.5, 0, 21, 0.5, 0, 0, 0, 0.5, 0, 10, 0, 0, 15.0, 0, 10, -0.1875, 1.5, 4, 1, 0, 1.5, 4, 1, 0, 1.5, 4, 0, 1, 1, -2, 1.5, 4, 21, 0, -0.1875, 10

In [15]:
"""
Running Agent simulations
"""
from Agents.AgentRandom2 import AgentRandom2
from Agents.AgentMCTS import AgentMCTS
from Agents.AgentUCT import AgentUCT
from Agents.AgentNoMoves import AgentNoMoves
from Agents.AgentModel import AgentMultiModel, AgentModel
from Game.CatanGame import *
from CatanSimulator import CreateGame
from DeepLearning.PPO import MaskablePPO
from Game.CatanPlayer import PlayerStatsTracker
from tabulate import tabulate
from DeepLearning.Stats import headers
import dill as pickle
import pandas as pd
from CatanData.GameStateViewer import SaveGameStateImage, DisplayImage
import time
import math
from DeepLearning.GetObservation import getObservationSimplified
from collections import deque


# best_model = AgentMultiModel("P1", 1, model=MaskablePPO.load("DeepLearning/Models/NoSetup/NoSetupDenseRewardEnv-10M.zip"), setupModel=MaskablePPO.load("DeepLearning/Models/Setup/SetupRandom_wins_1M.zip"), fullSetup=False)

winner = [0,0,0,0]
player0Stats = PlayerStatsTracker()
Player0LosingStats = PlayerStatsTracker()
player1Stats = PlayerStatsTracker()

players = [ AgentModel("P0", 0, model=MaskablePPO.load("DeepLearning/Models/SelfPlaySame/model_iteration_3800.zip")),
            AgentModel("P1", 1, model=MaskablePPO.load("DeepLearning/Models/SelfPlaySame/model_iteration_3796.zip")),
            AgentModel("P2", 2, model=MaskablePPO.load("DeepLearning/Models/SelfPlaySame/model_iteration_3796.zip")),
            AgentModel("P3", 3, model=MaskablePPO.load("DeepLearning/Models/SelfPlaySame/model_iteration_3796.zip")),]

COLLECT_STATS = True
numTurns = 0
for episode in range(50):
    game = CreateGame(players)
    game = pickle.loads(pickle.dumps(game, -1))
    while True:
        currPlayer = game.gameState.players[game.gameState.currPlayer]

        agentAction = currPlayer.DoMove(game)
        agentAction.ApplyAction(game.gameState)

        # if currPlayer.seatNumber == 0 and agentAction.type == 'EndTurn':
        #     DisplayImage(game.gameState, agentAction)
        #     time.sleep(1)
        #     numTurns += 1

        if game.gameState.currState == "OVER":
            break
    
    # print("Winner: ", game.gameState.winner)
    winner[game.gameState.winner] += 1
    lost = game.gameState.winner != 0

    # Stats
    if COLLECT_STATS:
        game.gameState.players[0].generatePlayerStats()
        game.gameState.players[1].generatePlayerStats()

        player0Stats += game.gameState.players[0].stats
        player1Stats += game.gameState.players[1].stats
        if lost:
            Player0LosingStats += game.gameState.players[0].stats

# Collect stats
if COLLECT_STATS:
    player0Stats.getAverages()
    Player0LosingStats.getAverages()
    player1Stats.getAverages()
    player0Data = player0Stats.getList()
    player0LosingData = Player0LosingStats.getList()
    player1Data = player1Stats.getList()

    p_hat0 = winner[0] / sum(winner)
    p_hat1 = winner[1] / sum(winner)
    margin_error0 = round(100*(1.96 * math.sqrt((p_hat0 * (1 - p_hat0)) / sum(winner))), 2)
    margin_error1 = round(100*(1.96 * math.sqrt((p_hat1 * (1 - p_hat1)) / sum(winner))), 2)
    player0Data.insert(0, margin_error0)
    player0LosingData.insert(0, -1)
    player1Data.insert(0, margin_error1)
    player0Data.insert(0, winner[0]/sum(winner))
    player0LosingData.insert(0, -1)
    player1Data.insert(0, winner[1]/sum(winner))
    player0Data.insert(0, "Player0")
    player0LosingData.insert(0, "Player0LossesStats")
    player1Data.insert(0, "Player1")

    table = tabulate([player0Data, player0LosingData, player1Data], headers=headers, tablefmt='simple')
    print(table)

print(f"\nNum turns: {numTurns}")

print("\n\nWinnings: ", winner)


# Brick, ore, wool, wheat, wood

AgentName             WinRate    MarginError    numTurns    victoryPoints    numRoadsBuilt    devCardsBought  usedDevCards                        settlementsBuilt    citiesBuilt    devCardVP    largestArmy    longestRoad  resourcesReceived                           totalResourcesReceivedPerTurn    totalResourcesDiscarded    totalResourcesStolen  resourcesFromDevCard            totalResourcesFromDevCard  resourcesFromBankTrade                 totalResourcesFromBankTrade  finalResourceProduction             finalTradeRates                                                                                       setupResourceProduction               totalSetupResourceProduction  setupTradeRates              setupResourceDiversity    turnsForFirstSettlement    noSettlementsBuilt    turnsForFirstCity    noCitysBuilt
------------------  ---------  -------------  ----------  ---------------  ---------------  ----------------  --------------------------------  ------------------  -------------  --

In [8]:
# # Save to csv
# fileName = f'Rewards_SetupVpActionDenseTrades_18M.csv'
# df = pd.DataFrame([player0Data, player0LosingData, player1Data], columns=headers)
# df.to_csv(f'DeepLearning/Data/Full/{fileName}', index=False)

# from DeepLearning.GetActionMask import allActionsDict

# print(allActionsDict)

model.save("DeepLearning/Models/SelfPlaySame/Final")

